In [1]:
from ckonlpy.tag import Twitter
import pickle
import re
import sys
from gensim.models import TfidfModel
from gensim.models import Word2Vec
from gensim.corpora import Dictionary
from pprint import pprint
from collections import Counter
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import LatentDirichletAllocation
import mglearn
from pprint import pprint
from ckonlpy.tag import Twitter
import numpy as np
import gc
import copy

class Social_analysis():
    
    non_bmp_map = dict.fromkeys(range(0x10000, sys.maxunicode + 1), 0xfffd)

    def __init__(self):
        self.twitter = Twitter()
        
    def pickle_to_table(self, filename):
        with open(filename, 'rb') as f:
            data = pickle.load(f)
        data = data[1:]
        for idx, i in enumerate(data):
            data[idx][2] = i[2].replace('#', ' ').translate(self.non_bmp_map)
            data[idx][3] = '/'.join(i[3])
            data[idx][4] = '/'.join(i[4])
        self.raw_data = np.array(data)
  
    def hashtags_split(self, hashtags):        
        hashtags_split = []
        for i in hashtags:
            hashtags_split.append(i.split('/'))
        
        hashtags_list = []
        
        for i in hashtags_split:
            temp = []
            for j in i:
                if self.isHangul(j):
                    t_hashtags = j.translate(self.non_bmp_map)
                    temp.append(t_hashtags)
            hashtags_list.append(temp)
        self.hashtags_list = hashtags_list
        
        return hashtags_list
                    
    def add_keyword_dic(self, keyword_list, tag='Noun'):
        for i in keyword_list:
            if type(i) == tuple:
                self.twitter.add_dictionary(i[0], i[1])
            else:
                self.twitter.add_dictionary(i, tag)
        
    def morph_pos(self, text_list, exception_list = ['맛', '밥', '물', '몸']):
        
        morph_list = []
        noun_list = []
        adj_list = []
        verb_list = []
        
        for j in text_list:
            parsed = self.twitter.pos(j)
            temp = []
            n_temp = []
            adj_temp = []
            verb_temp = []
            
            for i in parsed:
                if self.isHangul(i[0]):
                    if ((len(i[0]) > 1) or (i[0] in exception_list)):
                        temp.append(i)
                        if i[1] == 'Noun':
                            n_temp.append(i[0])
                        elif i[1] == 'Verb':
                            adj_temp.append(i[0])
                        elif i[1] == 'Adjective':
                            verb_temp.append(i[0])
                    else:
                        print('{} 제외'.format(i[0]))
                else: print('{} 한글이 아님.'.format(i[0]))
            

            morph_list.append(temp)
            noun_list.append(n_temp)
            adj_list.append(adj_temp)
            verb_list.append(verb_temp)

        nav_list = noun_list + adj_list + verb_list

        return morph_list, nav_list, noun_list, adj_list, verb_list

    def merge_list(self, tokenized_list):
        return [j for i in tokenized_list for j in i]

    
    def join_list(self, tokenized_list):
        joined_list = []
        for idx, i in enumerate(tokenized_list):
            joined_list.append(" ".join(i))
        return joined_list
 
    def split_list(self, untokenized_list):
        hashtag_splited = []
        for idx, i in enumerate(untokenized):
            hashtag_splited.append(i.split('/'))
            return hastag_splited

    def word_substitute(self, dataset, sublist):
        dataset = copy.deepcopy(dataset)
        sub_book = dict()
        for i in sublist:
            for j in i['sub_words']:
                sub_book[j] = i['main']
        gc.collect()
        for n, i in enumerate(dataset):
            dataset[n] = [sub_book.get(item,item) for item in i]

        del sub_book
        gc.collect()

        return dataset
    
    def word_delete(self, dataset, del_list):
        dataset = copy.deepcopy(dataset)

        for n, line in enumerate(dataset):
             dataset[n] = [i for i in line if i not in del_list]

        return dataset

    
    def isHangul(self, text):
        encText = text
        hanCount = len(re.findall(u'[\u3130-\u318F\uAC00-\uD7A3]+', encText))
        return hanCount > 0

    

class SB_Word2Vec():    
    
    def __init__(self, morph_list):
        self.dct = Dictionary(morph_list)
        self.corpus = [self.dct.doc2bow(line) for line in morph_list]
        self.build_Word2Vec(morph_list)
    
    def make_Word2Vec(self, morph_list, size=50, window=2, min_count=10, iteration=100):
        self.em = Word2Vec(morph_list, size=size, window=window, min_count=min_count, iter=iteration)
        self.em_vocab = list(self.em.wv.vocab.keys())
        self.em_vocab_dic = {word:idx for idx, word in enumerate(self.em_vocab)}

    def make_Word2Sen_matrix(self): 
        vocab_size = len(self.em_vocab)
        self.sen_matrix = np.zeros((len(self.corpus), vocab_size))
        for idx, row in enumerate(self.sen_matrix):
            for idx2, frequency in self.corpus[idx]:
                    if self.dct[idx2] in self.em_vocab:
                        self.sen_matrix[idx][self.em_vocab_dic[self.dct[idx2]]] = frequency                
        self.sim_matrix = np.zeros((vocab_size, vocab_size))
        for idx, w1 in enumerate(self.em_vocab):
            for idx2, w2 in enumerate(self.em_vocab):
                self.sim_matrix[idx][idx2] =  self.em.wv.similarity(w1, w2)

        self.word2sen_matrix = np.dot(self.sim_matrix, np.transpose(self.sen_matrix))

        return self.word2sen_matrix

    def get_sim_sen(self, keyword, main_text, number=1):
        self.sim_sen_index = np.argsort(self.word2sen_matrix[self.em_vocab_dic[keyword]])
        self.most_sim_sen_index = np.argmax(self.word2sen_matrix[self.em_vocab_dic[keyword]])
        index_list = self.sim_sen_index.reshape((-1,)).tolist()
        index_list.reverse()
        
        for idx, i in enumerate(index_list[:number]):
            print(str(idx + 1))
            print(main_text[i])
        return index_list
    
    def build_Word2Vec(self, morph_list):
        self.make_Word2Vec(morph_list)
        self.make_Word2Sen_matrix()
        
        
class SB_LDA():

    def make_lda(self, morph_joined, ntopic=10, learning_method='batch', max_iter=25, random_state=0, n_words=20):        
        self.vect = CountVectorizer(max_features=10000, max_df=.15)
        self.X = self.vect.fit_transform(morph_joined)
        self.lda = LatentDirichletAllocation(n_components=ntopic, learning_method=learning_method, max_iter=max_iter, random_state=random_state)
        self.document_topics = self.lda.fit_transform(self.X)
        self.sorting = np.argsort(self.lda.components_, axis=1)[:, ::-1]
        self.feature_names = np.array(self.vect.get_feature_names())
        mglearn.tools.print_topics(topics=range(ntopic), feature_names=self.feature_names, sorting=self.sorting, topics_per_chunk=5, n_words=n_words)

    def related_doc(self, main_text_list, topic_index, number=10):
        category = np.argsort(self.document_topics[:, topic_index])[::-1]
        related_docs = []
        for i in category[:number]:
            print(i)
            print(main_text_list[i] + ".\n")
            related_docs.append((i, main_text_list[i]))
        return related_docs

class SB_Tfidf():    
    
    def __init__(self, list_morph_merged):
        self.list_morph_merged = list_morph_merged
        self.dct = Dictionary(self.list_morph_merged)
        self.corpus = [self.dct.doc2bow(line) for line in self.list_morph_merged]

    def get_tfidf(self):       
        self.model = TfidfModel(self.corpus)
        self.tfidf = []
        for i in self.corpus:
             self.tfidf.append(sorted(self.model[i], key = lambda x: x[1], reverse=True))
        self.tfidf_hangul = []
        for idx1, i in enumerate(self.tfidf):
            self.tfidf_hangul.append([(self.dct[j[0]], j[1]) for j in i])        
        
        return self.tfidf_hangul
    
def frequency(merged):
    word_count = Counter(merged)
    word_count2 = []
    for i in word_count:
        word_count2.append((i, word_count[i]))
    word_count2 = sorted(word_count2, key=lambda x: x[1], reverse = True)
    return word_count2

C:\Users\abys\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [2]:
intake = Social_analysis()

In [3]:
labnosh = Social_analysis()

## DB에서 불러온 데이터를 Social_analysis 인스턴스에 등록해도  되고,  그냥 그 데이터로 앞으로 진행해도 된다. 일단 튜토리얼은 pickle 데이터로 진행하기 때문에 아래 함수를 실행하면 intake.row_data 에 저장이 된다. 이 놈은 DB에 들어간 놈이 비슷하게 생긴 놈이다.

In [4]:
intake.pickle_to_table('Data/intake_list.txt')

In [5]:
labnosh.pickle_to_table('Data/labnosh_list.txt')

## 형태소 분석에 꼭 포함하고 싶은 단어를 추가한다. 기본적으로는 hashtag들을 noun으로 추가한다. 여기서 해쉬태그 중에 포함하고 싶지 않은 것을 빼는 것을 추천한다.

In [6]:
intake.hashtag_splited = intake.hashtags_split(intake.raw_data[:, 3])
print(np.shape(intake.hashtag_splited))
print(intake.hashtag_splited[0])

(5235,)
['아침식사', '죽', '모닝죽', '단호박', '인테이크', '맛스타그램', '먹스타그램', '식사대용', '다이어트', '두통', '좋아요반사', '맛집', '간편식', '아점', '아픔', '선팔은맞팔', '맛스타', '선팔', '맞팔', '먹스타', '음식', '푸드스타그램', '좋반']


In [7]:
labnosh.hashtag_splited = labnosh.hashtags_split(labnosh.raw_data[:, 3])
print(np.shape(labnosh.hashtag_splited))
print(labnosh.hashtag_splited[0])

(7967,)
['와이식단', '와이_받았다그램', '에잇템', '푸드바', '푸드바', '프로틴바', '푸드바', '푸드바', '에잇템', '랩노쉬', '초코바', '프로틴', '다이어트', '식단', '다이어트식단', '식단관리', '건강식', '다이어트그램', '다이어터그램', '다이어트계정', '다이어트소통', '다이어트기록']


## intake.add_dic_keyword() 함수는 1차원 list를 받는다.
## 데이터의 형태는 ['단어', '단어', '단어'] or [('단어', Tag), ('단어', Tag)]
## Tag는 'Noun', 'Verb', 'Adjective' 등이 있다.

In [8]:
intake.hashtag_merged = intake.merge_list(intake.hashtag_splited)

intake.add_keyword_dic(intake.hashtag_splited)

In [9]:
labnosh.hashtag_merged = labnosh.merge_list(labnosh.hashtag_splited)

labnosh.add_keyword_dic(labnosh.hashtag_splited)

## 형태소 분석을 진행한다. 한글자는 제외시키는데 혹시 필요하다고 판단되는 글자는 exception_list 파라미터에 리스트로 넣어주면 된다.

In [10]:
intake.morph_list, intake.nav_list, intake.noun_list, intake.adj_list, intake.verb_list= intake.morph_pos(intake.raw_data[:, 2], exception_list=['맛', '밥', '물', '몸', '죽'])

lora 한글이 아님.
. 한글이 아님.
study 한글이 아님.
. 한글이 아님.
몇 제외
년 제외
째 제외
먹 제외
는 제외
엔 제외
하 제외
고 제외
도 제외
데 제외
면 제외
� 한글이 아님.
가 제외
데 제외
.. 한글이 아님.
다 제외
랑 제외
가 제외
오 제외
� 한글이 아님.
1122 한글이 아님.
_ 한글이 아님.
asm 한글이 아님.
. 한글이 아님.
고 제외
, 한글이 아님.
. 한글이 아님.
먹 제외
을 제외
수 제외
수 제외
요 제외
! 한글이 아님.
는 제외
일 제외
요 제외
. 한글이 아님.
감 제외
있 제외
게 제외
! 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
makemysugar 한글이 아님.
. 한글이 아님.
한 제외
잔 제외
� 한글이 아님.
! 한글이 아님.
~~ 한글이 아님.
먹 제외
는 제외
것 제외
가 제외
틈 제외
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
oats 한글이 아님.
oatmeal 한글이 아님.
oasis 한글이 아님.
_ 한글이 아님.
jaeyoon 한글이 아님.
짜 제외
. 한글이 아님.
로 제외
다 제외
. 한글이 아님.
이 제외
. 한글이 아님.
khjhmom 한글이 아님.
_ 한글이 아님.
을 제외
워 제외
시 제외
기 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
ㅎ 제외
leeminwk 한글이 아님.
차 제외
받 제외
음 제외
. 한글이 아님.
은 제외
만 제외
한 제외
질 제외
vveun 한글이 아님.
제 제외
술 제외
안 제외
�� 한글이 아님.
_ 한글이 아님.
si 한글이 아님.
1 한글이 아님.
ver 한글이 아님.
_ 한글이 아님.
star 한글이 아님.
1 한글이 아님.
일 제외
1 한글이 아님.
식 제외
딱 제외
넘 제외
( 한글이 아님.
๑॔˃̶◡ 한글이 아님.
˂̶๑॓ 한글이 아님.
) 한글이 아님.
◞♡ 한글이 아님.
kyu 한글이 아님.
_ 한글이 아님

ohn 한글이 아님.
___ 한글이 아님.
ohn 한글이 아님.
랑 제외
! 한글이 아님.
는 제외
, 한글이 아님.
, 한글이 아님.
다 제외
입 제외
에 제외
잘 제외
서 제외
그 제외
다 제외
. 한글이 아님.
우 제외
바 제외
티 제외
는 제외
이 제외
서 제외
왕 제외
였 제외
지 제외
... 한글이 아님.
� 한글이 아님.
는 제외
0 한글이 아님.
%, 한글이 아님.
30 한글이 아님.
% 한글이 아님.
있 제외
때 제외
용 제외
좋 제외
다 제외
. 한글이 아님.
배 제외
가 제외
... 한글이 아님.
! 한글이 아님.
은 제외
! 한글이 아님.
ohhhhhni 한글이 아님.
05 한글이 아님.
넘 제외
먹 제외
열 제외
엇 제외
는 제외
데 제외
줄 제외
한 제외
로 제외
거 제외
고 제외
왜 제외
분 제외
서 제외
분 제외
이 제외
때 제외
준 제외
에 제외
효 제외
ㅜ 제외
❤ 한글이 아님.
( 한글이 아님.
;; 한글이 아님.
무 제외
튼 제외
) 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
selka 한글이 아님.
dailygram 한글이 아님.
by 한글이 아님.
_ 한글이 아님.
sos 한글이 아님.
7 한글이 아님.
! 한글이 아님.
빵 제외
� 한글이 아님.
랑 제외
을 제외
기 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
nelollis 한글이 아님.
2 한글이 아님.
후 제외
먹 제외
는 제외
컷 제외
! 한글이 아님.
서 제외
봄 제외
� 한글이 아님.
좋 제외
게 제외
있 제외
어 제외
들 제외
고 제외
다 제외
니 제외
기 제외
좋 제외
! 한글이 아님.
� 한글이 아님.
mint 한글이 아님.
. 한글이 아님.
shushu 한글이 아님.
73 한글이 아님.
kcal 한글이 아님.
...!!! 한글이 아님.
도 제외
. 한글이 아님.
❤️ 한글이 아님.
vellancchu 한글이 아님.
momsfit 한글이 아님.
_ 한글이 아님.
master

hoya 한글이 아님.
8929 한글이 아님.
daily 한글이 아님.
�� 한글이 아님.
zera 한글이 아님.
_ 한글이 아님.
fam 한글이 아님.
� 한글이 아님.
: 한글이 아님.
. 한글이 아님.
. 한글이 아님.
✨ 한글이 아님.
d 한글이 아님.
. 한글이 아님.
myday 한글이 아님.
_ 한글이 아님.
1027 한글이 아님.
� 한글이 아님.
2018 한글이 아님.
. 한글이 아님.
06 한글이 아님.
. 한글이 아님.
25 한글이 아님.
� 한글이 아님.
: 한글이 아님.
: 한글이 아님.
, 한글이 아님.
3 한글이 아님.
개 제외
, 한글이 아님.
, 한글이 아님.
, 한글이 아님.
콩 제외
: 한글이 아님.
: 한글이 아님.
- 한글이 아님.
쫌 제외
어 제외
욥 제외
. 한글이 아님.
집 제외
에 제외
먹 제외
을 제외
게 제외
하 제외
서 제외
이 제외
것 제외
저 제외
것 제외
어 제외
욥 제외
. 한글이 아님.
5 한글이 아님.
시 제외
배 제외
가 제외
어 제외
욥 제외
. 한글이 아님.
만 제외
주 제외
겠 제외
로 제외
퉁 제외
미 제외
서 제외
도 제외
먹 제외
꾸 제외
도 제외
거 제외
에 제외
욥 제외
. 한글이 아님.
잘 제외
이 제외
에 제외
욥 제외
. 한글이 아님.
- 한글이 아님.
은 제외
1 한글이 아님.
이 제외
권 제외
이 제외
에 제외
욥 제외
. 한글이 아님.
- 한글이 아님.
냄 제외
시 제외
가 제외
? 한글이 아님.
나 제외
데 제외
냄 제외
시 제외
가 제외
!!!! 한글이 아님.
- 한글이 아님.
➡️ 한글이 아님.
는 제외
앞 제외
어 제외
욥 제외
. 한글이 아님.
야 제외
. 한글이 아님.
rovvkzv 한글이 아님.
� 한글이 아님.
lulie 한글이 아님.
___. 한글이 아님.
.. 한글이 아님.
지 제외
.. 한글이 아님.
ㅋ 제외
. 한글이 아님.
. 한글이 아님.
고 제외
줄 제외
~ 한글이 아님.
. 한글이 아님.
d 한글이 아님.
_ 한글이 아님.
ddang 한글이 아님.

minigom 한글이 아님.
_ 한글이 아님.
07180622 한글이 아님.
이 제외
다 제외
준 제외
!!! 한글이 아님.
이 제외
거 제외
거 제외
!! 한글이 아님.
!! 한글이 아님.
잘 제외
습 제외
니 제외
닷 제외
� 한글이 아님.
tlj 한글이 아님.
_ 한글이 아님.
dunjeon 한글이 아님.
❤️ 한글이 아님.
hysuum 한글이 아님.
intake 한글이 아님.
j 한글이 아님.
___ 한글이 아님.
niii 한글이 아님.
+ 한글이 아님.
8 한글이 아님.
지 제외
겠 제외
... 한글이 아님.
d 한글이 아님.
. 한글이 아님.
myday 한글이 아님.
_ 한글이 아님.
1027 한글이 아님.
� 한글이 아님.
2018 한글이 아님.
. 한글이 아님.
06 한글이 아님.
. 한글이 아님.
21 한글이 아님.
� 한글이 아님.
: 한글이 아님.
, 한글이 아님.
: 한글이 아님.
, 한글이 아님.
, 한글이 아님.
2 한글이 아님.
개 제외
, 한글이 아님.
햄 제외
: 한글이 아님.
: 한글이 아님.
, 한글이 아님.
- 한글이 아님.
까 제외
불 제외
고 제외
이 제외
것 제외
저 제외
것 제외
났 제외
어 제외
욥 제외
. 한글이 아님.
중 제외
에 제외
간 제외
거 제외
? 한글이 아님.
.. 한글이 아님.
들 제외
오 제외
가 제외
품 제외
왔 제외
웩 제외
... 한글이 아님.
.. 한글이 아님.
내 제외
에 제외
욥 제외
. 한글이 아님.
- 한글이 아님.
되 제외
, 한글이 아님.
엔 제외
될 제외
지 제외
. 한글이 아님.
과 제외
않 제외
을 제외
. 한글이 아님.
에 제외
햄 제외
을 제외
의 제외
.... 한글이 아님.
을 제외
에 제외
이 제외
서 제외
... 한글이 아님.
아 제외
... 한글이 아님.
도 제외
야 제외
게 제외
잘 제외
어 제외
욥 제외
. 한글이 아님.
- 한글이 아님.
➡️ 한글이 아님.
싶 제외
어 제외
욥 제외
. 한글이 아님.
7411 한글이 아님.
_ 한글이 아님.
010 한글이 아님

comjirak 한글이 아님.
너 제외
와 제외
(!?) 한글이 아님.
다 제외
본 제외
건 제외
� 한글이 아님.
꿀 제외
> 한글이 아님.
> 한글이 아님.
콩 제외
gweonyeonhoHG 한글이 아님.
HG 한글이 아님.
SM 한글이 아님.
5 한글이 아님.
JSR 한글이 아님.
LF 한글이 아님.
BMW 한글이 아님.
에 제외
카 제외
치 제외
시 제외
고 제외
면 제외
더 제외
볼 제외
수 제외
있 제외
어 제외
오 제외
010 한글이 아님.
- 한글이 아님.
8526 한글이 아님.
- 한글이 아님.
0360 한글이 아님.
gweonyeonho 한글이 아님.
6 한글이 아님.
p 한글이 아님.
6 한글이 아님.
p 한글이 아님.
SM 한글이 아님.
5 한글이 아님.
JSR 한글이 아님.
LF 한글이 아님.
BMW 한글이 아님.
에 제외
카 제외
치 제외
시 제외
고 제외
면 제외
더 제외
볼 제외
수 제외
있 제외
어 제외
오 제외
010 한글이 아님.
- 한글이 아님.
8526 한글이 아님.
- 한글이 아님.
0360 한글이 아님.
gweonyeonhoAD 한글이 아님.
망 제외
SM 한글이 아님.
5 한글이 아님.
JSR 한글이 아님.
LF 한글이 아님.
BMW 한글이 아님.
에 제외
카 제외
치 제외
시 제외
고 제외
면 제외
더 제외
볼 제외
수 제외
있 제외
어 제외
오 제외
010 한글이 아님.
- 한글이 아님.
8526 한글이 아님.
- 한글이 아님.
0360 한글이 아님.
gweonyeonhoK 한글이 아님.
5 한글이 아님.
LED 한글이 아님.
K 한글이 아님.
5 한글이 아님.
SM 한글이 아님.
5 한글이 아님.
JSR 한글이 아님.
LF 한글이 아님.
BMW 한글이 아님.
에 제외
카 제외
치 제외
시 제외
고 제외
면 제외
더 제외
볼 제외
수 제외
있 제외
어 제외
오 제외
010 한글이 아님.
- 한글이 아님.
8526 한글이 아님.
- 한글이 아님.
0360 한글이 아님.
gweonyeonho 한글이 아님.
로 제외
J

...

intakefoods 한글이 아님.
! 한글이 아님.
!.! 한글이 아님.
. 한글이 아님.
는 제외
는 제외
분 제외
, 한글이 아님.
이 제외
신 제외
분 제외
들 제외
을 제외
위 제외
한 제외
을 제외
다 제외
! 한글이 아님.
. 한글이 아님.
는 제외
>< 한글이 아님.
. 한글이 아님.
b 한글이 아님.
. 한글이 아님.
saem 한글이 아님.
_ 한글이 아님.
내 제외
내 제외
들 제외
�� 한글이 아님.
, 한글이 아님.
도 제외
썼 제외
��� 한글이 아님.
. 한글이 아님.
b 한글이 아님.
. 한글이 아님.
saem 한글이 아님.
_ 한글이 아님.
로 제외
하 제외
는 제외
님 제외
기 제외
�� 한글이 아님.
. 한글이 아님.
lilunaa 한글이 아님.
_ 한글이 아님.
� 한글이 아님.
엔 제외
� 한글이 아님.
게 제외
! 한글이 아님.
다 제외
� 한글이 아님.
내 제외
랑 제외
@intakefoods 한글이 아님.
당 제외
❤ 한글이 아님.
차 제외
는 제외
만 제외
부 제외
으 제외
면 제외
능 제외
☕ 한글이 아님.
뭐 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
< 한글이 아님.
와 제외
차 제외
는 제외
다 제외
> 한글이 아님.
intakefoods 한글이 아님.
D 한글이 아님.
- 한글이 아님.
3 한글이 아님.
!!! 한글이 아님.
을 제외
하 제외
여 제외
를 제외
~! 한글이 아님.
. 한글이 아님.
2 한글이 아님.
. 한글이 아님.
0 한글이 아님.
을 제외
로 제외
가 제외
>< 한글이 아님.
. 한글이 아님.
https://www.facebook.com/shopintake 한글이 아님.
. 한글이 아님.
D 한글이 아님.
- 한글이 아님.
3 한글이 아님.
yoon 한글이 아님.
. 한글이 아님.
eunyoung 한글이 아님.
이 제외
거 제외
참 제외
도 제외
요 제외
intake 한글이 아님.
ncr 한글이 아님.
_ 한글이 아님.
motors 한글이 아님.
MD 한글이 아님.
1 한글

minishell 한글이 아님.
_ 한글이 아님.
u 한글이 아님.
gs 한글이 아님.
25 한글이 아님.
은 제외
내 제외
가 제외
이 제외
만 제외
lunch 한글이 아님.
yummy 한글이 아님.
koreanfood 한글이 아님.
kimbob 한글이 아님.
intakefoods 한글이 아님.
엔 제외
이 제외
짱 제외
겠 제외
음 제외
?.? 한글이 아님.
. 한글이 아님.
. 한글이 아님.
를 제외
주 제외
신 제외
@___eunbi 한글이 아님.
님 제외
!! 한글이 아님.
. 한글이 아님.
는 제외
는 제외
분 제외
, 한글이 아님.
이 제외
신 제외
분 제외
들 제외
을 제외
위 제외
한 제외
을 제외
다 제외
! 한글이 아님.
. 한글이 아님.
는 제외
>< 한글이 아님.
. 한글이 아님.
hyhy 한글이 아님.
_ 한글이 아님.
0906 한글이 아님.
나 제외
의 제외
을 제외
줄 제외
난 제외
❤️❤️ 한글이 아님.
intake 한글이 아님.
����� 한글이 아님.
intakefoods 한글이 아님.
가 제외
시 제외
졌 제외
한 제외
잔 제외
이 제외
!! 한글이 아님.
과 제외
향 제외
, 한글이 아님.
색 제외
을 제외
한 제외
을 제외
냅 제외
! 한글이 아님.
. 한글이 아님.
. 한글이 아님.
를 제외
주 제외
신 제외
@the 한글이 아님.
. 한글이 아님.
lovedragon 한글이 아님.
님 제외
. 한글이 아님.
・・・ 한글이 아님.
하 제외
고 제외
요 제외
☺️ 한글이 아님.
향 제외
도 제외
좋 제외
고 제외
좋 제외
고 제외
날 제외
딱 제외
이 제외
~ 한글이 아님.
요 제외
� 한글이 아님.
. 한글이 아님.
는 제외
는 제외
분 제외
, 한글이 아님.
이 제외
신 제외
분 제외
들 제외
을 제외
위 제외
한 제외
을 제외
다 제외
! 한글이 아님.
. 한글이 아님.
는 제외
>< 한글이 아님.
. 한글이 아님.
coffee 한글이 아님.
cafe 한글이 아님.
als 한글이 아님.
12040 한글이 아님.
나 

차 제외
만 제외
, 한글이 아님.
다 제외
들 제외
배 제외
고 제외
요 제외
!! 한글이 아님.
. 한글이 아님.
를 제외
주 제외
신 제외
@ksqm 한글이 아님.
님 제외
. 한글이 아님.
. 한글이 아님.
는 제외
는 제외
분 제외
, 한글이 아님.
이 제외
신 제외
분 제외
들 제외
을 제외
위 제외
한 제외
을 제외
다 제외
! 한글이 아님.
. 한글이 아님.
는 제외
>< 한글이 아님.
. 한글이 아님.
intakefoods 한글이 아님.
한 제외
요 제외
!! 한글이 아님.
!! 한글이 아님.
그 제외
중 제외
에 제외
눈 제외
에 제외
들 제외
!! 한글이 아님.
를 제외
주 제외
신 제외
@signora_hj 한글이 아님.
님 제외
!! 한글이 아님.
・・・ 한글이 아님.
☔️ 한글이 아님.
비 제외
가 제외
와 제외
서 제외
잘 제외
잤 제외
나 제외
� 한글이 아님.
이 제외
좋 제외
도 제외
군 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
는 제외
는 제외
분 제외
, 한글이 아님.
이 제외
신 제외
분 제외
들 제외
을 제외
위 제외
한 제외
을 제외
다 제외
! 한글이 아님.
. 한글이 아님.
는 제외
>< 한글이 아님.
. 한글이 아님.
smile 한글이 아님.
. 한글이 아님.
mommy 한글이 아님.
_ 한글이 아님.
의 제외
과 제외
딱 제외
이 제외
� 한글이 아님.
. 한글이 아님.
( 한글이 아님.
이 제외
은 제외
을 제외
) 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
intakefoods 한글이 아님.
먹 제외
말 제외
까 제외
는 제외
분 제외
들 제외
이 제외
이 제외
죠 제외
? 한글이 아님.
하 제외
지 제외
만 제외
딱 제외
!!! 한글이 아님.
가 제외
을 제외
고 제외
!! 한글이 아님.
. 한글이 아님.
를 제외
수 제외
도 제외
와 제외
겠 제외
! 한글이 아님.
. 한글이 아님.
는 제외
>< 한글이 아님.
. 한글이 아님.
콩 제외
inta

yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
� 한글이 아님.
Diet 한글이 아님.
+ 한글이 아님.
482 한글이 아님.
� 한글이 아님.
20151116 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
➡️ 한글이 아님.
1 한글이 아님.
/ 한글이 아님.
2 한글이 아님.
1 한글이 아님.
1 한글이 아님.
/ 한글이 아님.
2 한글이 아님.
2 한글이 아님.
5 한글이 아님.
1 한글이 아님.
컵 제외
➡️ 한글이 아님.
& 한글이 아님.
& 한글이 아님.
. 한글이 아님.
. 한글이 아님.
우 제외
히 제외
이 제외
가 제외
! 한글이 아님.
휘 제외
것 제외
! 한글이 아님.
에 제외
중 제외
고 제외
했 제외
었 제외
죠 제외
! 한글이 아님.
는 제외
구 제외
가 제외
주 제외
가 제외
� 한글이 아님.
밤 제외
! 한글이 아님.
요 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
dietfood 한글이 아님.
DANO 한글이 아님.
_ 한글이 아님.
_ 한글이 아님.
_ 한글이 아님.
�� 한글이 아님.
intakefoods 한글이 아님.
D 한글이 아님.
- 한글이 아님.
1 한글이 아님.
http://goo.gl/mwlWY2 한글이 아님.
workout 한글이 아님.
_ 한글이 아님.
byeun 한글이 아님.
의 제외
�� 한글이 아님.
한 제외
개 제외
와 제외
kartkiss 한글이 아님.
드 제외
ㅋ 제외
햇 제외
군 제외
ㅋ 제외
ㅋ 제외
ncr 한글이 아님.
_ 한글이 아님.
motorsGm 한글이 아님.
( 한글이 아님.
) 한글이 아님.
. 한글이 아님.
차 제외
car 한글이 아님.
cartuning 한글이 아님.
tuning 한글이 아님.
wheels 한글이 아님.
brake 한글이 아님.
suspension 한글이 아님.
gm 한글이 아님.
ncr 한글이 아님

yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
2015714 한글이 아님.
33 한글이 아님.
. 한글이 아님.
with 한글이 아님.
& 한글이 아님.
& 한글이 아님.
& 한글이 아님.
. 한글이 아님.
. 한글이 아님.
하 제외
고 제외
왔 제외
�� 한글이 아님.
이 제외
휘 제외
! 한글이 아님.
잘 제외
내 제외
을 제외
! 한글이 아님.
열 제외
운 제외
했 제외
배 제외
뭐 제외
먹 제외
한 제외
을 제외
겠 제외
:-) 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
님 제외
들 제외
용 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
dietfood 한글이 아님.
dieter 한글이 아님.
�� 한글이 아님.
yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
2015713 한글이 아님.
. 한글이 아님.
with 한글이 아님.
& 한글이 아님.
& 한글이 아님.
& 한글이 아님.
. 한글이 아님.
하 제외
고 제외
왔 제외
�� 한글이 아님.
은 제외
이 제외
고 제외
� 한글이 아님.
제 제외
가 제외
게 제외
은 제외
못 제외
... 한글이 아님.
간 제외
& 한글이 아님.
로 제외
을 제외
서 제외
는 제외
만 제외
이 제외
어 제외
졌 제외
뭐 제외
든 제외
가 제외
�� 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
님 제외
들 제외
용 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
dietfood 한글이 아님.
dieter 한글이 아님.
�� 한글이 아님.
yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
2015712 한글이 아님.
. 한글이 아님.
with 한글이 아님.
& 한글이 아님.
. 한글이 아님.
이 제외
히 제외
과 제외
후 제외
♥️

In [11]:
labnosh.morph_list, labnosh.nav_list, labnosh.noun_list, labnosh.adj_list, labnosh.verb_list= labnosh.morph_pos(labnosh.raw_data[:, 2], exception_list=['맛', '밥', '물', '몸', '죽'])

y 한글이 아님.
_ 한글이 아님.
diet 한글이 아님.
__ 한글이 아님.
20180504 한글이 아님.
� 한글이 아님.
✔️ 한글이 아님.
✔️ 한글이 아님.
한 제외
잔 제외
로 제외
된 제외
‼️ 한글이 아님.
�� 한글이 아님.
은 제외
! 한글이 아님.
" 한글이 아님.
갓 제외
띵 제외
템 제외
��‍♀️ 한글이 아님.
" 한글이 아님.
서 제외
는 제외
분 제외
들 제외
사 제외
주 제외
! 한글이 아님.
, 한글이 아님.
면 제외
에 제외
! 한글이 아님.
꾸 제외
덕 제외
, 한글이 아님.
도 제외
막 제외
도 제외
정 제외
에 제외
이 제외
있 제외
고 제외
, 한글이 아님.
있 제외
! 한글이 아님.
�� 한글이 아님.
95 한글이 아님.
% 한글이 아님.
이 제외
로 제외
기 제외
에 제외
수 제외
, 한글이 아님.
200 한글이 아님.
kcal 한글이 아님.
에 제외
가 제외
11 한글이 아님.
g 한글이 아님.
( 한글이 아님.
44 한글이 아님.
%), 한글이 아님.
13 한글이 아님.
g 한글이 아님.
( 한글이 아님.
24 한글이 아님.
%) 한글이 아님.
등 제외
도 제외
..! 한글이 아님.
�� 한글이 아님.
는 제외
9 한글이 아님.
g 한글이 아님.
( 한글이 아님.
9 한글이 아님.
%) 한글이 아님.
, 한글이 아님.
단 제외
걸 제외
아 제외
니 제외
를 제외
다 제외
갈 제외
때 제외
쯤 제외
서 제외
(?) 한글이 아님.
는 제외
을 제외
! 한글이 아님.
땐 제외
한 제외
주 제외
면 제외
마 제외
을 제외
바 제외
✨ 한글이 아님.
또 제외
도 제외
보 제외
서 제외
님 제외
께 제외
넘 제외
한 제외
주 제외
셔 제외
서 제외
❤️ 한글이 아님.
‼️ 한글이 아님.
다 제외
면 제외
할 제외
거 제외
!! 한글이 아님.
는 제외
꼭 제외
요 제외
! 한글이 아님.
실 제외
거 제외
� 한글이 아님.
한 제외
끼 제외
로 제외
, 한글이 아님.
에 제외
당 제외
때 제외
면 제외
딱 제외
좋 제외
을 제

c 한글이 아님.
646 한글이 아님.
a 한글이 아님.
왔 제외
다 제외
!!!!!! 한글이 아님.
freedhot 한글이 아님.
77 한글이 아님.
[ 한글이 아님.
] 한글이 아님.
에 제외
당 제외
_ 한글이 아님.
에 제외
때 제외
에 제외
를 제외
잔 제외
서 제외
당 제외
을 제외
했 제외
. 한글이 아님.
로 제외
당 제외
가 제외
에 제외
서 제외
.. 한글이 아님.
.. 한글이 아님.
그 제외
찌 제외
고 제외
_ 한글이 아님.
가 제외
을 제외
할 제외
때 제외
도 제외
늘 제외
를 제외
.. 한글이 아님.
�� 한글이 아님.
_ 한글이 아님.
을 제외
, 한글이 아님.
당 제외
을 제외
의 제외
가 제외
즙 제외
! 한글이 아님.
_ 한글이 아님.
이 제외
참 제외
. 한글이 아님.
책 제외
에 제외
밭 제외
을 제외
에 제외
좋 제외
은 제외
를 제외
는 제외
인 제외
것 제외
요 제외
. 한글이 아님.
_ 한글이 아님.
만 제외
봐 제외
도 제외
의 제외
을 제외
한 제외
듯 제외
한 제외
, 한글이 아님.
한 제외
빛 제외
을 제외
요 제외
. 한글이 아님.
아 제외
는 제외
고 제외
둔 제외
탁 제외
산 제외
요 제외
. 한글이 아님.
_ 한글이 아님.
thanks 한글이 아님.
to 한글이 아님.
@_hollish_ 한글이 아님.
_ 한글이 아님.
More 한글이 아님.
information 한글이 아님.
about 한글이 아님.
pumpkin 한글이 아님.
juice 한글이 아님.
@atemshop 한글이 아님.
. 한글이 아님.
official 한글이 아님.
_ 한글이 아님.
I 한글이 아님.
chose 한글이 아님.
fresh 한글이 아님.
pumpkin 한글이 아님.
juice 한글이 아님.
to 한글이 아님.
replenish 한글이 아님.
sugar 한글이 아님.
healthily 한글이 아님.
. 한글이 아님.
_ 한글이 아님.
pumpkinjuice 한글이 아님.
juicestagram 한글이 아님.
healthyf

. 한글이 아님.
. 한글이 아님.
적 제외
� 한글이 아님.
diet 한글이 아님.
dietfood 한글이 아님.
foodstagram 한글이 아님.
sowon 한글이 아님.
. 한글이 아님.
s 한글이 아님.
labnosh 한글이 아님.
오 제외
! 한글이 아님.
labnosh 한글이 아님.
. 한글이 아님.
official 한글이 아님.
. 한글이 아님.
@soowainii 한글이 아님.
님 제외
� 한글이 아님.
. 한글이 아님.
비 제외
가 제외
� 한글이 아님.
요 제외
❤️ 한글이 아님.
. 한글이 아님.
의 제외
SNS 한글이 아님.
에 제외
속 제외
한 제외
을 제외
와 제외
요 제외
! 한글이 아님.
램 제외
되 제외
신 제외
분 제외
께 제외
는 제외
로 제외
요 제외
. 한글이 아님.
. 한글이 아님.
labnosh 한글이 아님.
marie 한글이 아님.
_ 한글이 아님.
godiet 한글이 아님.
한 제외
산 제외
. 한글이 아님.
전 제외
샀 제외
던 제외
랑 제외
당 제외
이 제외
나 제외
씩 제외
했 제외
던 제외
것 제외
�� 한글이 아님.
. 한글이 아님.
의 제외
가 제외
.... 한글이 아님.
d 한글이 아님.
._. 한글이 아님.
lil 한글이 아님.
. 한글이 아님.
2018 한글이 아님.
. 한글이 아님.
07 한글이 아님.
. 한글이 아님.
02 한글이 아님.
� 한글이 아님.
- 한글이 아님.
: 한글이 아님.
: 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
짤 제외
힘 제외
1 한글이 아님.
도 제외
는 제외
요 제외
. 한글이 아님.
올 제외
병 제외
에 제외
! 한글이 아님.
... 한글이 아님.
� 한글이 아님.
겠 제외
띵 제외
요 제외
̈ 한글이 아님.
(* 한글이 아님.
˙˘˙ 한글이 아님.
) 한글이 아님.
♡ 한글이 아님.
diet 한글이 아님.
_ 한글이 아님.
gf 한글이 아님.
180702 한글이 아님.
⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀ 한글이 아님.
에 제외
⠀⠀⠀⠀⠀⠀⠀

mybong 한글이 아님.
_ 한글이 아님.
s 한글이 아님.
2 한글이 아님.
20180630 한글이 아님.
: 한글이 아님.
서 제외
: 한글이 아님.
100 한글이 아님.
g 한글이 아님.
더 제외
, 한글이 아님.
( 한글이 아님.
노 제외
), 한글이 아님.
- 한글이 아님.
볼 제외
때 제외
랑 제외
서 제외
싶 제외
게 제외
더 제외
나 제외
을 제외
듯 제외
왔 제외
다 제외
. 한글이 아님.
안 제외
며 제외
본 제외
안 제외
.. 한글이 아님.
� 한글이 아님.
가 제외
산 제외
걸 제외
로 제외
♥️ 한글이 아님.
야 제외
.. 한글이 아님.
핵 제외
.... 한글이 아님.
한 제외
이 제외
... 한글이 아님.
은 제외
���� 한글이 아님.
다 제외
! 한글이 아님.
에 제외
좋 제외
은 제외
먹 제외
는 제외
덜 제외
게 제외
않 제외
~~ 한글이 아님.
넘 제외
다 제외
>_< 한글이 아님.
적 제외
! 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
uu 한글이 아님.
_ 한글이 아님.
ding 한글이 아님.
. 한글이 아님.
� 한글이 아님.
이 제외
날 제외
은 제외
고 제외
니 제외
면 제외
(?) 한글이 아님.
- 한글이 아님.
, 한글이 아님.
♥️ 한글이 아님.
- 한글이 아님.
에 제외
면 제외
를 제외
놓 제외
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
& 한글이 아님.
�� 한글이 아님.
. 한글이 아님.
heeya 한글이 아님.
_ 한글이 아님.
su 한글이 아님.
� 한글이 아님.
diet 한글이 아님.
_ 한글이 아님.
tommy 한글이 아님.
18 한글이 아님.
. 한글이 아님.
06 한글이 아님.
. 한글이 아님.
30 한글이 아님.
: 한글이 아님.
볼 제외
이 제외
것 제외
저 제외
것 제외
다 제외
서 제외
탱 제외
도 제외
좋 제외
고 제외
좋 제외
고 제외
저 제외
이 제외
짱 제외
�� 한글이 아님.
거 제외
로 제외
망 제외
고 

marina 한글이 아님.
_ 한글이 아님.
dieter 한글이 아님.
20180628 한글이 아님.
. 한글이 아님.
. 한글이 아님.
� 한글이 아님.
찹 제외
+ 한글이 아님.
. 한글이 아님.
. 한글이 아님.
�‍♀️ 한글이 아님.
� 한글이 아님.
� 한글이 아님.
무 제외
나 제외
없 제외
는 제외
� 한글이 아님.
+ 한글이 아님.
. 한글이 아님.
. 한글이 아님.
(@woori_hada 한글이 아님.
) 한글이 아님.
찹 제외
. 한글이 아님.
로 제외
고 제외
위 제외
에 제외
콩 제외
+ 한글이 아님.
. 한글이 아님.
도 제외
실 제외
면 제외
더 제외
. 한글이 아님.
서 제외
때 제외
로 제외
도 제외
담 제외
엔 제외
로 제외
쟁 제외
여 제외
둬 제외
야 제외
겠 제외
어 제외
. 한글이 아님.
. 한글이 아님.
JMT 한글이 아님.
jjin 한글이 아님.
9 한글이 아님.
_ 한글이 아님.
daily 한글이 아님.
자 제외
4 한글이 아님.
안 제외
것 제외
다 제외
,, 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
_ 한글이 아님.
ooooo 한글이 아님.
. 한글이 아님.
20180627 한글이 아님.
. 한글이 아님.
수 제외
� 한글이 아님.
< 한글이 아님.
템 제외
7 한글이 아님.
6 한글이 아님.
> 한글이 아님.
▪️ 한글이 아님.
당 제외
( 한글이 아님.
) 한글이 아님.
▪️ 한글이 아님.
황 제외
. 한글이 아님.
. 한글이 아님.
D 한글이 아님.
- 한글이 아님.
122 한글이 아님.
도 제외
끝 제외
�� 한글이 아님.
요 제외
�� 한글이 아님.
들 제외
:) 한글이 아님.
. 한글이 아님.
. 한글이 아님.
▫️ 한글이 아님.
처 제외
@atemshop 한글이 아님.
. 한글이 아님.
official 한글이 아님.
. 한글이 아님.
. 한글이 아님.
▫️ 한글이 아님.
❌ 한글이 아님.
술 제외
❌ 한글이 아님.
▫️ 한글이 아님.
☺️ 한글이 아님.
▫️ 한글이 아님.
지 제외
@se

...

lucy 한글이 아님.
_ 한글이 아님.
kang 한글이 아님.
1012 한글이 아님.
을 제외
잘 제외
다 제외
야 제외
... 한글이 아님.
전 제외
에 제외
없 제외
잘 제외
지 제외
..? 한글이 아님.
안 제외
^^... 한글이 아님.
labnosh 한글이 아님.
coco 한글이 아님.
__ 한글이 아님.
nenne 한글이 아님.
_ 한글이 아님.
90 한글이 아님.
, 한글이 아님.
, 한글이 아님.
세 제외
다 제외
2 한글이 아님.
회 제외
날 제외
에 제외
뭘 제외
니 제외
룩 제외
안 제외
니 제외
이 제외
없 제외
고 제외
한 제외
! 한글이 아님.
잘 제외
�✨ 한글이 아님.
taeyeop 한글이 아님.
_ 한글이 아님.
yoon 한글이 아님.
. 한글이 아님.
비 제외
오 제외
는 제외
날 제외
��� 한글이 아님.
. 한글이 아님.
_ 한글이 아님.
_ 한글이 아님.
_ 한글이 아님.
비 제외
humming 한글이 아님.
_ 한글이 아님.
u 한글이 아님.
야 제외
하 제외
.... 한글이 아님.
�� 한글이 아님.
atemshop 한글이 아님.
. 한글이 아님.
official 한글이 아님.
. 한글이 아님.
[ 한글이 아님.
Mini 한글이 아님.
Bar 한글이 아님.
in 한글이 아님.
] 한글이 아님.
� 한글이 아님.
가 제외
왔 제외
! 한글이 아님.
에 제외
바 제외
람 제외
!!!!! 한글이 아님.
✋� 한글이 아님.
. 한글이 아님.
는 제외
28 한글이 아님.
( 한글이 아님.
목 제외
) 한글이 아님.
엔 제외
간 제외
거 제외
.. 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
thehyundai 한글이 아님.
stylishfood 한글이 아님.
labnosh 한글이 아님.
futurefood 한글이 아님.
food 한글이 아님.
gymlife 한글이 아님.
open 한글이 아님.
. 한글이 아님.
platform 한글이 아님.
면 제외
먹 제외
야 제외
겠 제외
죵 제외
.. 한글이 아님.


verygoodnyang 한글이 아님.
용 제외
는 제외
분 제외
들 제외
은 제외
요 제외
~ 한글이 아님.
한 제외
글 제외
은 제외
제 제외
에 제외
있 제외
^_^ 한글이 아님.
갠 제외
적 제외
가 제외
.. 한글이 아님.
�☺️ 한글이 아님.
labnosh 한글이 아님.
jyophie 한글이 아님.
� 한글이 아님.
에 제외
! 한글이 아님.
� 한글이 아님.
. 한글이 아님.
내 제외
에 제외
이 제외
나 제외
서 제외
와 제외
☄ 한글이 아님.
yay 한글이 아님.
! 한글이 아님.
는 제외
에 제외
자 제외
�✨ 한글이 아님.
by 한글이 아님.
_ 한글이 아님.
j 한글이 아님.
1125 한글이 아님.
다 제외
할 제외
꺼 제외
야 제외
... 한글이 아님.
� 한글이 아님.
soo 한글이 아님.
_ 한글이 아님.
4363 한글이 아님.
다 제외
할 제외
산 제외
, 한글이 아님.
어 제외
째 제외
.. 한글이 아님.
이 제외
될 제외
거 제외
.. 한글이 아님.
� 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
LABNOSH 한글이 아님.
Fennec 한글이 아님.
atemshop 한글이 아님.
. 한글이 아님.
official 한글이 아님.
. 한글이 아님.
D 한글이 아님.
- 한글이 아님.
2 한글이 아님.
� 한글이 아님.
수 제외
말 제외
다 제외
! 한글이 아님.
든 제외
볼 제외
수 제외
요 제외
!! 한글이 아님.
속 제외
에 제외
가 제외
� 한글이 아님.
. 한글이 아님.
� 한글이 아님.
도 제외
있 제외
! 한글이 아님.
첫 제외
주 제외
�� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
labnosh 한글이 아님.
futurefood 한글이 아님.
food 한글이 아님.
kimjye 한글이 아님.
_ 한글이 아님.
h 한글이 아님.
땐 제외
1 한글이 아님.
샀 제외
음 제외
!! 한글이 아님.
꽤 제외
좀 제외
는 제외
게 제외
이 제외
했 제외
음 제외
labnosh 한글이 아님.
shi

mjbeneat 한글이 아님.
, 한글이 아님.
, 한글이 아님.
다 제외
��� 한글이 아님.
atemshop 한글이 아님.
. 한글이 아님.
official 한글이 아님.
� 한글이 아님.
. 한글이 아님.
�� 한글이 아님.
자 제외
및 제외
이 제외
고 제외
있 제외
! 한글이 아님.
� 한글이 아님.
의 제외
을 제외
길 제외
! 한글이 아님.
�� 한글이 아님.
. 한글이 아님.
labnosh.com 한글이 아님.
. 한글이 아님.
MAKE 한글이 아님.
EAT 한글이 아님.
SIMPLE 한글이 아님.
LABNOSH 한글이 아님.
THEFUTUREFOOD 한글이 아님.
gif 한글이 아님.
makeeatsimple 한글이 아님.
restday 한글이 아님.
LABNOSH 한글이 아님.
dahye_abc@hwan.26 한글이 아님.
어 제외
도 제외
좋 제외
군 제외
atemshop 한글이 아님.
. 한글이 아님.
official 한글이 아님.
Repost 한글이 아님.
@tattooist_ida 한글이 아님.
with 한글이 아님.
@repostapp 한글이 아님.
. 한글이 아님.
・・・ 한글이 아님.
. 한글이 아님.
다 제외
에 제외
두 제외
번 제외
을 제외
데 제외
가 제외
준 제외
한 제외
들 제외
은 제외
힘 제외
도 제외
못 제외
쓴 제외
다 제외
민 제외
진 제외
이 제외
고 제외
군 제외
! 한글이 아님.
. 한글이 아님.
. 한글이 아님.
Ida 한글이 아님.
님 제외
! 한글이 아님.
의 제외
! 한글이 아님.
. 한글이 아님.
와 제외
길 제외
! 한글이 아님.
makeeatsimple 한글이 아님.
make 한글이 아님.
eat 한글이 아님.
simple 한글이 아님.
적 제외
인 제외
합 제외
! 한글이 아님.
. 한글이 아님.
LABNOSH 한글이 아님.
의 제외
� 한글이 아님.
. 한글이 아님.
중 제외
몇 제외
몇 제외
분 제외
들 제외
의 제외
를 제외
다 제외
! 한글이 아님.
� 한글이 아님.
들 제외
요 제외

hyezzixxi 한글이 아님.
서 제외
고 제외
당 제외
... 한글이 아님.
... 한글이 아님.
날 제외
... 한글이 아님.
한 제외
끼 제외
먹 제외
을 제외
수 제외
록 제외
데 제외
둑 제외
안 제외
듯 제외
? 한글이 아님.
때 제외
다 제외
니 제외
면 제외
좋 제외
을 제외
것 제외
더 제외
labnosh 한글이 아님.
08 한글이 아님.
l 한글이 아님.
bandaltokki 한글이 아님.
들 제외
먹 제외
서 제외
은 제외
과 제외
, 한글이 아님.
3 한글이 아님.
이 제외
좋 제외
겠 제외
을 제외
했 제외
었 제외
딱 제외
인 제외
듯 제외
� 한글이 아님.
을 제외
뿐 제외
이 제외
, 한글이 아님.
가 제외
수 제외
! 한글이 아님.
labnosh 한글이 아님.
08 한글이 아님.
l 한글이 아님.
mjbeneat 한글이 아님.
yuhamig 한글이 아님.
! 한글이 아님.
! 한글이 아님.
mjbeneat 한글이 아님.
mls 한글이 아님.
makelifesimple 한글이 아님.
mjbeneat 한글이 아님.
��� 한글이 아님.
있 제외
� 한글이 아님.
jungjaewoon 한글이 아님.
뭐 제외
다 제외
labnosh 한글이 아님.
cat 한글이 아님.
daily 한글이 아님.
. 한글이 아님.
nana 한글이 아님.
또 제외
�� 한글이 아님.
못 제외
했 제외
분 제외
들 제외
을 제외
가 제외
:-) 한글이 아님.
✌�️ 한글이 아님.
늘 제외
한 제외
것 제외
뿐 제외
도 제외
은 제외
무 제외
익 제외
한 제외
것 제외
요 제외
riverbae 한글이 아님.
labnosh 한글이 아님.
color 한글이 아님.
design 한글이 아님.
package 한글이 아님.
와 제외
한 제외
! 한글이 아님.
에 제외
세 제외
다 제외
또 제외
원 제외
들 제외
도 제외
고 제외
였 제외
다 제외
능 제외
b 한글이 아님.
@labnosh_mj 한글이 아님.
옹 제외
♥ 한글이 아님.
어 제외
mjbeneat 한글이 아님

jyophie 한글이 아님.
1 한글이 아님.
. 한글이 아님.
만 제외
한 제외
번 제외
병 제외
을 제외
� 한글이 아님.
2 한글이 아님.
. 한글이 아님.
들 제외
��� 한글이 아님.
�� 한글이 아님.
도 제외
되 제외
고 제외
도 제외
! 한글이 아님.
우 제외
앙 제외
� 한글이 아님.
데 제외
또 제외
� 한글이 아님.
만 제외
는 제외
이 제외
넘 제외
. 한글이 아님.
는 제외
� 한글이 아님.
lubsun 한글이 아님.
을 제외
좀 제외
겠 제외
다 제외
던 제외
에 제외
알 제외
게 제외
된 제외
한 제외
나 제외
이 제외
라 제외
의 제외
, 한글이 아님.
등 제외
을 제외
에 제외
면 제외
된 제외
다 제외
! 한글이 아님.
때 제외
, 한글이 아님.
서 제외
때 제외
먹 제외
좋 제외
을 제외
듯 제외
!!! 한글이 아님.
08 한글이 아님.
L 한글이 아님.
daily 한글이 아님.
dailygram 한글이 아님.
labnosh 한글이 아님.
healthy 한글이 아님.
strong 한글이 아님.
fitness 한글이 아님.
jyophie 한글이 아님.
���� 한글이 아님.
에 제외
. 한글이 아님.
아 제외
도 제외
. 한글이 아님.
� 한글이 아님.
에 제외
다 제외
전 제외
에 제외
� 한글이 아님.
참 제외
해 제외
��� 한글이 아님.
yoga 한글이 아님.
makelifesimple 한글이 아님.
labnosh 한글이 아님.
futurefood 한글이 아님.
@ 한글이 아님.
즈 제외
daily 한글이 아님.
. 한글이 아님.
nana 한글이 아님.
내 제외
게 제외
될 제외
:) 한글이 아님.
1 한글이 아님.
weekplan 한글이 아님.
! 한글이 아님.
7 한글이 아님.
개 제외
의 제외
5 한글이 아님.
개 제외
의 제외
이 제외
내 제외
�� 한글이 아님.
08 한글이 아님.
L 한글이 아님.
beanyh 한글이 아님.
는 제외
LabNosh 한글이 아님.
걍 제외
줄 제외
알 제외
았 제외
, 한글이 아님

## 빈도분석에는 merge된 list가 필요하다.

In [12]:
intake.nav_merged = intake.merge_list(intake.nav_list)

intake.nav_frequency = frequency(intake.nav_merged)

print(intake.nav_frequency [:5])

[('인테이크', 5727), ('다이어트', 2167), ('밀스', 1490), ('아침', 1273), ('모닝죽', 1212)]


In [13]:
labnosh.nav_merged = labnosh.merge_list(labnosh.nav_list)

labnosh.nav_frequency = frequency(labnosh.nav_merged)

print(labnosh.nav_frequency [:5])

[('랩노쉬', 10886), ('다이어트', 2730), ('맛', 1694), ('미래형식사', 1628), ('올리브영', 1355)]


## 여기서 내가 형태소분석시에 안짤리게 할 단어와 제외하고 싶은 단어, 대체하고 싶은 단어를 선택한다.
## 안짤리게 할 단어는 다시 위로 돌아가 추가한다.
## 대체하고 싶은 단어와 제외하고 싶은 단어는 아래 방법으로 처리한다. 일단 생략한다.

## 분석에서 제외할 단어를 리스트로 넣어준다. 인자로 넣어주는 값은 변하지 않으므로 넣어보고 마음에 안들면 다시 intake.nav_list 로 접근하면 삭제 전 파일로 돌아갈 수 있다.
## 진짜 후회없을 것 같을 때, intake.nav_list에 업데이트 하도록 하자.

In [14]:
intake.nav_list[0]

['아침식사',
 '죽',
 '모닝죽',
 '단호박',
 '인테이크',
 '모닝죽',
 '아침',
 '기도',
 '입맛',
 '요거',
 '하나',
 '아침',
 '뚝딱',
 '맛은',
 '여러',
 '종류',
 '맛있는데',
 '굳이',
 '단호박이',
 '꿀고구마']

In [15]:
intake.nav_frequency = frequency(intake.nav_merged)

In [16]:
intake.nav_frequency [:5]

[('인테이크', 5727), ('다이어트', 2167), ('밀스', 1490), ('아침', 1273), ('모닝죽', 1212)]

In [17]:
modified_nav_list = intake.word_delete(intake.nav_list, ['요거', '여러', '굳이'])
print(modified_nav_list[0])

['아침식사', '죽', '모닝죽', '단호박', '인테이크', '모닝죽', '아침', '기도', '입맛', '하나', '아침', '뚝딱', '맛은', '종류', '맛있는데', '단호박이', '꿀고구마']


## 이번에는 단어를 대체하는 것, 리스트 안에 딕셔너리 형식
#### [{'main': '최종적으로 대체하고 싶은 단어', 'sub_words':['대체할 단어', '대체할 단어']},
####  {'main': '최종적으로 대체하고 싶은 단어', 'sub_words':['대체할 단어', '대체할 단어']}]

In [18]:
modified_nav_list_2 = intake.word_substitute(modified_nav_list, [{'main':'모닝죽', 'sub_words':['단호박', '단호박이', '꿀고구마']}])
print(modified_nav_list_2[0])

['아침식사', '죽', '모닝죽', '모닝죽', '인테이크', '모닝죽', '아침', '기도', '입맛', '하나', '아침', '뚝딱', '맛은', '종류', '맛있는데', '모닝죽', '모닝죽']


### 토픽모델링은 조인된 것이 필요하다.
### join_list 를 통해서 만들기

In [23]:
intake.morph_joined = intake.join_list(intake.nav_list)

In [24]:
labnosh.morph_joined = labnosh.join_list(labnosh.nav_list)

### 파라미터는 다음과 같다. 
#### self.make_lda(self, morph_joined, ntopic=10, learning_method='batch', max_iter=25, random_state=0, n_words=20)
#### ntopic과 n_words를 넣어주면 몇개의 토픽으로 나눌지, 몇개의 단어를 보여줄지를 정할 수 있다.

In [60]:
intake.LDA = SB_LDA()
intake.LDA.make_lda(intake.morph_joined, ntopic=10)

topic 0       topic 1       topic 2       topic 3       topic 4       
--------      --------      --------      --------      --------      
모닝죽           힘내            있는            다이어트          건강            
아침            운동            많은            저녁            다이어트          
일상            시켜            입니            다이어터          구매            
먹스타그램         않아            있어            점심            먹스타그램         
다이어트          먹겠            같아            들어오시          맛스타그램         
단호박           타서            이벤트           다이어트그램        링크            
간식            주문했           씨씨앙           1개            데일리           
고구마           않는            아니            먹고            유산균           
데일리           씹어            괜찮            받은            건강식           
맛스타그램         드시            없는            사과            후기            
소통            찍어            있다            함께하는          선물            
단호박죽          정모            참여            고구마           간식            
식단조절  

In [ ]:
labnosh.LDA = SB_LDA()
labnosh.LDA.make_lda(labnosh.morph_joined, ntopic=10)

### 그 토픽과 관련된 문서 10개를 보여준다. 두번째 인자는 토픽의 인덱스이고 세번째 인덱스는 보여줄 포스팅의 개수이다.

In [ ]:
topic0 = intake.LDA.related_doc(intake.raw_data[:,2], 0, 4)

In [ ]:
topic0 = labnosh.LDA.related_doc(labnosh.raw_data[:,2], 0, 4)

### 데이터 형식은 같고 할 줄 알겠지?

In [19]:
intake.SB_word2vec = SB_Word2Vec(intake.nav_list)

intake.flavor = intake.SB_word2vec.get_sim_sen('맛', intake.raw_data[:,2], 4)

1
ulimyu-
드디어 5개를 다 먹었당!!
-
� 밀스3.0 코코넛
-
일단 나는 밀스2.0 라이트 애용자임.
2.0라이트는 54g/202kcal + 우유 200ml/150kcal
2.0은 92g/400kcal + 우유 300ml/200kcal
3.0은 95g/400kcal + 우유 300ml/200kcal
우유랑 밀스한통먹으면 600kcal 이네..
그냥 밥먹자 � 맛난백반정식1끼 �
-
코코넛은 기존의 밀스랑 맛은 비슷한데
코코넛뿌스레기가 있어서 씹으면 달달한 맛이 남.
물론 기존에 씹던 다른 견과도 좀 씹힌다.
맛있음.
먹을만함.
배부름.
이건 추천한다.
근데 코코넛칩 싫어하는 사람은 먹지마라.
처음부터 끝까지 마시는동안 골고루 씹힌다.
기존에 밀스 먹는 사람은 사먹어도 �아깝지 않을듯.
어차피 2.0 곧 단종될거라서 3.0 사먹어야뎀. -
-
� 밀스3.0 핑크
-
모두가 예상한 딸기맛이다.
근데 뭔가 딸기 아이스크림 녹인 맛. 뭔가 2% 부족한 딸기맛.
밀스+딸기분말.
견과류 씹히는건 똑같다.
처음엔 좀 거부감이 드는데, 먹다보니 또 의외로 괜찮다.
지난 밀스2.0 핑크 에디션의 실패 이후로 노력을 한듯하다.
2.0핑크보다 나아 ㅋㅋㅋ 왜지 왜때문이지 ㅋㅋㅋ
하지만 둘다 돈주고 사먹으라면 나는 코코넛을 사먹겠다. -
-
� 밀스3.0 그린
-
이름처럼 그린답게 색상도 그린그림함.
일단 밀스처럼 견과씹히는거 똑같다.
이전의 밀스2.0 후레시그린 보다 더 그린그린함.. 치커리맛인지 쑥맛인지 왠지 풀맛이 더 많이 난다.
선식같은 느낌도 있음.
풀을 싫어한다면 거부감이 있을 수 있음.
나쁘지 않음. 먹을만함.
하지만 돈주고 사먹으라면 나는 차라리 코코넛을 먹겠어. -
-
� 밀스3.0 소이
-
딱히 할말이 없다.
콩맛나는 미숫가루인데, 두유맛이 진하게 날 줄 알았는데 그건 아니다.
기존 밀스에서 뭔가 진한맛이 빠진느낌.(물에 타먹어서 그런가) -
-
� 밀스3.0 그레인
-
맛은 기존의 밀스와 제일 흡사하다.
더하고 빼고 할말이 없다.
2
junes840

In [20]:
labnosh.SB_word2vec = SB_Word2Vec(labnosh.nav_list)

labnosh.flavor = labnosh.SB_word2vec.get_sim_sen('맛', labnosh.raw_data[:,2], 4)

1
diet_baki 받았다그램  랩노쉬플랫바
이거 뭐야...신세계다♥
.
� 영양정보
� 1개 33g 기준
칼로리 : 130kcal
탄수화물 : 14g
(당류 : 9g)
단백질 : 12g
지방 : 3.2g
나트륨 : 120mg
.
� 영양성분 Review
우선 제가 제일 먼저 보는
원재료명 및 함량을 살펴봤습니다�
제가 합성첨가물이나 합성착색료 등에 민감보스잖아요!
다른 것보다 판토텐산칼슘, 말토덱스트린, 황산망간이 보이더라구용�
식품안전정보포털을 통해서 확인한결과
판토텐산칼슘은 B5(비타민종류)고
말토덱스트린은 글리코겐 재합성을 위한 안전한 식품
황산망간도 이유식에 쓰일 정도로 법률산 안전하다고 하니
우선 만족�
.
칼로리는 1개 기준 130kcal고,
당류는 9g 이에요
당류함량이 살짝 아쉽지만�
해외 제품들에 비하면 적당한 수준이에요!
.
사실 제가 식품선택기준이 왕엄격한 편이라 그렇지
전체적으로 괜찮다고 판단됩니다�
.
� 맛 Review
맛은....정말 신세계...�
저녁이라서 리뷰를 위해
쪼끔만 맛보려고 했는데 다 먹었어요...��
.
제 기준 단백질바에서 중요한 점은
단백질 비린내가 나냐 안나냐인데 단백질바 맞나요!?
어떻게든 냄새를 찾아보고자 열심히 먹었지만(변명)
비린내 어디? 그냥 정말 맛있었어요...완전 맛있음�
.
향은 고소고소했구요!
씹을 때 피넛버터 맛이 나고 크런키에서 초콜렛 벗긴 맛이랑도
비슷하고 쫀득하고 달달구리하고...
식감은 쫀득하면서 크런치해요!
너무 바삭거리지도 않고 너무 쫀득하지도 않고
이에 달라붙지 않아서 좋았어요♥️
.
왜 다들 랩노쉬 플랫바 엄지척 하시는지 한방에 이해�
진짜 맛있더라구요(맛있다고만 한 10번 하는 듯 합니다)
다이어터가 아니었다면 오늘 한박스 클리어했을 맛입니다
강추...��
.
같이 보내주신 푸드바도 깨알리뷰 해보겠습니다!
 랩노쉬푸드바 .
� 영양정보
� 1개 53g 기준
칼로리 : 200kcal
탄수화물 : 25g
(당류 : 9g)
단백질 : 13g
지방 : 8g
나트륨 : 75mg
.
� 

In [21]:
intake.SB_word2vec.em.wv.most_similar('맛') 

[('맛은', 0.6681041717529297),
 ('식감', 0.6280479431152344),
 ('생각보다', 0.6160725355148315),
 ('새콤달콤', 0.6123064756393433),
 ('미숫가루', 0.5867149829864502),
 ('단맛', 0.5775174498558044),
 ('단점', 0.5737367868423462),
 ('고소', 0.5660829544067383),
 ('조금', 0.5660343170166016),
 ('약간', 0.5656855702400208)]

most_similar(positive=None, negative=None, topn=10, restrict_vocab=None, indexer=None)¶

model.wv.most_similar(positive=['woman', 'king'], negative=['man'])
[('queen', 0.50882536), ...]

model.wv.most_similar_cosmul(positive=['woman', 'king'], negative=['man'])
[('queen', 0.71382287), ...]


model.wv.doesnt_match("breakfast cereal dinner lunch".split())
'cereal'

In [22]:
intake.SB_word2vec.em.wv.most_similar(positive=['아침', '맛'], negative=['운동'])

[('미숫가루', 0.5826406478881836),
 ('생각보다', 0.579865574836731),
 ('심지어', 0.5629949569702148),
 ('귀리', 0.5474948883056641),
 ('완전', 0.5468454957008362),
 ('아주', 0.5345592498779297),
 ('맛나', 0.5310249328613281),
 ('그냥', 0.5308135747909546),
 ('일단', 0.5180487036705017),
 ('좋아', 0.5167618989944458)]

## TFIDF에는 merge 된 리스트를 넣어서 비교해주면 된다. 
## intake만 있어서 패스
## 토픽모델링 된 애들끼리 비교해보는 것도 좋을 듯.

In [23]:
tfidf = SB_Tfidf([intake.nav_merged, labnosh.nav_merged])
tfidf.get_tfidf()
tfidf_of_all = tfidf.tfidf_hangul

for i in tfidf_of_all:
    pprint(i[:10])
    print()

[('흡기', 0.25419146503600865),
 ('튜닝', 0.23128150466795636),
 ('좋은', 0.2160081977559215),
 ('파워젤부스트', 0.18764348491928534),
 ('카스타그램', 0.1800068314632679),
 ('자동차', 0.17346112850096726),
 ('아미노리커버', 0.1680063760323834),
 ('먹으면', 0.16364257405751628),
 ('단팥죽', 0.13418691072716335),
 ('머플러', 0.13091405924601301)]

[('으로', 0.4224923468565074),
 ('쇼콜라', 0.34686938659387423),
 ('미식당', 0.3169824681667258),
 ('많이', 0.22822737708004256),
 ('맛이', 0.19471780187384585),
 ('그래놀라요거트', 0.18384983153670095),
 ('자색고구마', 0.18203850314717682),
 ('푸드쉐이크', 0.17162336490741298),
 ('그린씨리얼', 0.16664221183622158),
 ('함께', 0.13856662179859727)]



In [1]:
labnosh = Social_analysis('labnosh.txt', 'labnosh.official')

meals = Social_analysis('meals.txt', 'intakefoods')

morningjuk = Social_analysis('morningjuk.txt', 'intakefoods')

easy_food = Social_analysis('easy_food.txt')

conven_food = Social_analysis('conven_food.txt')

keywords = [intake, labnosh, meals, morningjuk, easy_food, conven_food]

### 빈도분석

for i in keywords:
    print(len(i.main_text_list), len(i.morph_merged))

labnosh.morph_frequency = analyzer.frequency(labnosh.morph_merged)
pprint(labnosh.morph_frequency)

meals.morph_frequency = analyzer.frequency(meals.morph_merged)
pprint(meals.morph_frequency)

morningjuk.morph_frequency = analyzer.frequency(morningjuk.morph_merged)
pprint(morningjuk.morph_frequency)

easy_food.morph_frequency = analyzer.frequency(easy_food.morph_merged)
pprint(easy_food.morph_frequency)

conven_food.morph_frequency = analyzer.frequency(conven_food.morph_merged)
pprint(conven_food.morph_frequency)

### 토픽모델링

intake.LDA = analyzer.SB_LDA()
intake.LDA.make_lda(intake.morph_joined, ntopic=10)

topic0 = intake.LDA.related_doc(intake.main_text_list, 0)

topic1 = intake.LDA.related_doc(intake.main_text_list, 1)

topic2 = intake.LDA.related_doc(intake.main_text_list, 2)

topic3 = intake.LDA.related_doc(intake.main_text_list, 3)

topic7 = intake.LDA.related_doc(intake.main_text_list, 7)

topic9 = intake.LDA.related_doc(intake.main_text_list, 9)

topic3 = intake.LDA.related_doc(intake.main_text_list, 3)



labnosh.LDA = analyzer.SB_LDA()
labnosh.LDA.make_lda(labnosh.morph_joined, ntopic=10)

meals.LDA = analyzer.SB_LDA()
meals.LDA.make_lda(meals.morph_joined, ntopic=10)

morningjuk.LDA = analyzer.SB_LDA()
morningjuk.LDA.make_lda(morningjuk.morph_joined, ntopic=10)

easy_food.LDA = analyzer.SB_LDA()
easy_food.LDA.make_lda(easy_food.morph_joined, ntopic=10)

conven_food.LDA = analyzer.SB_LDA()
conven_food.LDA.make_lda(conven_food.morph_joined, ntopic=10)

### Word2Vec

intake.SB_word2vec = analyzer.SB_Word2Vec(intake.hashtags_appended)

intake.flavor = intake.SB_word2vec.get_sim_sen('맛', intake.main_hash_dic, intake.main_text_list, 4)


intake.diet = intake.SB_word2vec.get_sim_sen('다이어트', intake.main_hash_dic, intake.main_text_list, 4)


intake.health = intake.SB_word2vec.get_sim_sen('건강', intake.main_hash_dic, intake.main_text_list, 4)


intake.exercise = intake.SB_word2vec.get_sim_sen('운동', intake.main_hash_dic, intake.main_text_list, 4)


intake.morningjuk = intake.SB_word2vec.get_sim_sen('모닝죽', intake.main_hash_dic, intake.main_text_list, 4)


intake.meals = intake.SB_word2vec.get_sim_sen('밀스', intake.main_hash_dic, intake.main_text_list, 4)


intake.gonyak = intake.SB_word2vec.get_sim_sen('곤약젤리', intake.main_hash_dic, intake.main_text_list, 4)




### TFIDF

tfidf = analyzer.SB_Tfidf([intake.morph_merged, labnosh.morph_merged, meals.morph_merged, morningjuk.morph_merged, easy_food.morph_merged, conven_food.morph_merged])

tfidf_of_all = tfidf.tfidf_hangul

for i in tfidf_of_all:
    pprint(i[:10])
    print()

meals_juk_SB_Tfidf = analyzer.SB_Tfidf([meals.morph_merged, morningjuk.morph_merged])

tfidf_meals_juk = meals_juk_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_juk:
    pprint(i[:10])
    print()

intake_meals_SB_Tfidf = analyzer.SB_Tfidf([intake.morph_merged, meals.morph_merged])

tfidf_intake_meals = intake_meals_SB_Tfidf.tfidf_hangul

for i in tfidf_intake_meals:
    pprint(i[:10])
    print()

intake_morningjuk_SB_Tfidf = analyzer.SB_Tfidf([intake.morph_merged, morningjuk.morph_merged])

tfidf_intake_morningjuk = intake_morningjuk_SB_Tfidf.tfidf_hangul

for i in tfidf_intake_morningjuk:
    pprint(i[:10])
    print()

meals_conven_food_SB_Tfidf = analyzer.SB_Tfidf([meals.morph_merged, conven_food.morph_merged])

tfidf_meals_conven_food = meals_conven_food_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_conven_food:
    pprint(i[:10])
    print()

morningjuk_conven_food_SB_Tfidf = analyzer.SB_Tfidf([morningjuk.morph_merged, conven_food.morph_merged])

tfidf_morningjuk_conven_food = morningjuk_conven_food_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_conven_food:
    pprint(i[:10])
    print()

C:\Users\abys\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [9]:
import csv
with open('morph_list.csv', 'w', encoding='utf-8') as f:
    spamwriter = csv.writer(f, delimiter=' ',
                            quotechar='|', quoting=csv.QUOTE_MINIMAL)
    for i in intake.morph_list:
        spamwriter.writerow(i)

In [16]:
def morph_pos(text_list, add_list, del_list, exception_list = ['맛', '밥', '물', '몸']):
    morph_list = []
    noun_list = []
    adj_list = []
    verb_list = []

    for j in text_list:
        parsed = self.twitter.pos(j)
        temp = []
        n_temp = []
        adj_temp = []
        verb_temp = []

        for i in parsed:
            if self.isHangul(i):
                if not i[0] in del_list:
                    if len(i[0]) > 1:
                        temp.append(i)
                        if i[1] == 'Noun':
                            n_temp.append(i[0])
                        elif i[1] == 'Verb':
                            n_adj.append(i[0])
                        elif i[1] == 'Adjective':
                            n_verb.append(i[0])

                    elif i in exception_list:
                        temp.append(i)
            else: print(i, '한글이 아닙니다.')

        morph_list.append(temp)
        noun_list.append(n_temp)
        adj_list.append(adj_temp)
        verb_list.append(verb_temp)


    nav_list = noun_list + adj_list + verb_list

    return morph_list, nav_list, noun_list, adj_list, verb_list

In [ ]:

    '''def get_from_dic(self, filename):
        self.data = handler.load_by_pickle(filename)
        self.dataset, self.dataset_dic, self.main_text_list, self.morph_list, self.morph_merged, self.morph_joined, self.hashtags_merged, self.hashtags_appended, self.main_hash_dic = handler.create_datasets_with_dic(self.data)

        # dataset, main_text_list, morph_list, morph_merged, morph_joined, hashtags_merged, hashtags_appended, main_hash_dic
    def get_data_from_list(self, filename, add_list, del_list):
        self.data = handler.load_by_pickle(filename)
        self.dataset, self.main_text_list, self.morph_list, self.morph_merged, self.morph_joined, self.hashtags_merged, self.hashtags_appended, self.main_hash_dic = handler.create_datasets_with_list(self.data[1:], add_list, del_list)'''
